# Hierarchical Representations in AAT 

**The Getty AAT does not explicitly use the common SKOS properties `skos:boarder` and `skos:narrower` to denote the hierarchical relations** between its concepts. Instead it uses `gpv:narrower`and `gpv:broader`. However skos hierarchies are possible to query via [Getty SPAQL web UI](https://vocab.getty.edu/sparql) with inference enabled, as these SKOS relations are inferred.


It possible to query Getty AAT SPARQL endpoint (via [web UI](https://vocab.getty.edu/sparql))  for this relations, if we enable inference ([see query](https://vocab.getty.edu/queries?toc=&query=%23+find+subject+with+skos%3Anarrower+relationships+to+other+subject+%0D%0A%0D%0APREFIX+skos%3A+%3Chttp%3A%2F%2Fwww.w3.org%2F2004%2F02%2Fskos%2Fcore%23%3E%0D%0A%0D%0ASELECT+*%0D%0AWHERE+%7B%0D%0A++++%3Fs+skos%3Anarrower+%3Fo+.%0D%0A%7D%0D%0ALIMIT+10&implicit=true&equivalent=false#Finding_Subjects)). If querying the Getty AAT SPARQL endpoint remotely, like we try in [sparql/aat_narrower.ttl](sparql/aat_narrower.ttl), we cannot rely on inferred statements, hence we get zero results from that query.


![skos relations inferred](img/inference-skos.png) source: https://www.getty.edu/research/tools/vocabularies/lod/aat_semantic_representation.pdf / https://vocab.getty.edu/doc/


## Do we need SKOS?

Since for the use case of the SSHOC, where a user is offered terms in the dataverse key words, we can disregard the  hierarchical relations of AAT. Instead we shall focus on **What terms we want to offer**. And look how to capture them.  


# What AAT terms we want to offer?

## Subject_Hierarchy AAT
https://vocab.getty.edu/doc/#Subject_Hierarchy

## produce a submodule of AAT
and include it in SKOSMOS




In [23]:
# prefixes and functions

from pprint import pprint
from SPARQLWrapper import SPARQLWrapper, JSON, TURTLE, CSV 

prefixes = '''    
PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>
PREFIX aat: <http://vocab.getty.edu/aat/>
PREFIX gvp: <http://vocab.getty.edu/ontology#> 
PREFIX skos: <http://www.w3.org/2004/02/skos/core#>
PREFIX skosxl: <http://www.w3.org/2008/05/skos-xl#>
PREFIX dcterms: <http://purl.org/dc/terms/>
'''    


def sparql_query(query, format):
    formats = {"json": JSON, "turtle": TURTLE, "csv": CSV}
    f_ = formats[format]
    endpoint = "http://vocab.getty.edu/sparql"
    sparql = SPARQLWrapper(endpoint)

    query = prefixes + query     
    sparql.setQuery(query)

    sparql.setReturnFormat(f_)
    results = sparql.query().convert()    
    # sparql.setReturnFormat(XML)
    # results = sparql.query()
    return results
    # # Print the results
    # print("Subject ID: ", subjectID)
    # 


def print_sparql_results(results):
    for row in results["results"]["bindings"]:
        return (row)

count_subjs = sparql_query(query="SELECT (COUNT(?concept) as ?conceptcount) WHERE {?concept a gvp:Concept . }", format='json')
print(count_subjs)
# print(f'all subjects: {count_subjs['results']['bindings'][0]['count']['value']}')

all_subjects = sparql_query(query="SELECT ?concept WHERE {?concept a gvp:Concept . } ORDER BY ?concept LIMIT 10", format='json')
print_sparql_results(all_subjects)

# all_subjects_ = sparql_query(query="SELECT * WHERE {?concept a gvp:Concept. ?s ?p ?concept} ORDER BY ?concept LIMIT 1")
# print_sparql_results(all_subjects)

# print(count_subjects.print_results())


{'head': {'vars': ['conceptcount']}, 'results': {'bindings': [{'conceptcount': {'datatype': 'http://www.w3.org/2001/XMLSchema#integer', 'type': 'literal', 'value': '56876'}}]}}


{'concept': {'type': 'uri', 'value': 'http://vocab.getty.edu/aat/300000202'}}

In [22]:
# SELECT QUERY: GETTY AAT Concepts with labels in EN and NL 
# lang: @en-US is converted to @en 

pref_label_query = '''
SELECT ?concept

WHERE {
      ?concept a gvp:Concept ;
              skos:inScheme aat: ;
              skosxl:prefLabel ?preflabel . 

              
    { ?preflabel  dcterms:language aat:300388277 ;
                  skosxl:literalForm ?label_literal_en. } # lang: @en
                 
    UNION

    { ?preflabel  dcterms:language aat:300387822 ;
                  skosxl:literalForm ?label_literal_en_us . 
      BIND (STRLANG(STR(?label_literal_en_us), 'en') AS  ?label_literal_en)} # lang: @en-US - converts to @en
    
    UNION
    
    { ?preflabel  dcterms:language aat:300388256 ;
                  skosxl:literalForm ?label_literal_nl . } # lang: @nl 

}


''' 

subjs_w_preflable = sparql_query(query=pref_label_query, format='json')
print(subjs_w_preflable)


# BROKEN CELL

{'head': {'vars': ['concept']}, 'results': {'bindings': [{'concept': {'type': 'uri', 'value': 'http://vocab.getty.edu/aat/300189559'}}, {'concept': {'type': 'uri', 'value': 'http://vocab.getty.edu/aat/300189557'}}, {'concept': {'type': 'uri', 'value': 'http://vocab.getty.edu/aat/300451373'}}, {'concept': {'type': 'uri', 'value': 'http://vocab.getty.edu/aat/300451618'}}, {'concept': {'type': 'uri', 'value': 'http://vocab.getty.edu/aat/300451464'}}, {'concept': {'type': 'uri', 'value': 'http://vocab.getty.edu/aat/300456608'}}, {'concept': {'type': 'uri', 'value': 'http://vocab.getty.edu/aat/300451694'}}, {'concept': {'type': 'uri', 'value': 'http://vocab.getty.edu/aat/300451703'}}, {'concept': {'type': 'uri', 'value': 'http://vocab.getty.edu/aat/300266528'}}, {'concept': {'type': 'uri', 'value': 'http://vocab.getty.edu/aat/300451770'}}, {'concept': {'type': 'uri', 'value': 'http://vocab.getty.edu/aat/300452069'}}, {'concept': {'type': 'uri', 'value': 'http://vocab.getty.edu/aat/300452091

In [1]:
# CONSTRUCT QUERY: GETTY AAT Concepts - slim  
# AAT gvp:concepts with labels in EN and NL become a skos:concept with rdfs:label @en @nl
# lang: @en-US is converted to @en 

pref_label_query = '''
CONSTRUCT {
    # TODO: change concept scheme from aat:
    
    <https://vocabularies.dans.knaw.nl/aatconcepts> 
        rdfs:label "The Art and Architecture Thesaurus Concepts Scheme" ;
        dct:created "2025-01-07"^^xsd:date ;
        dct:creator <https://dans.knaw.nl/en/> , <https://orcid.org/0000-0002-7839-3698> ; 
        vann:preferredNamespacePrefix "aatc" ;
        vann:preferredNamespaceUri "https://vocabularies.dans.knaw.nl/aatconcepts" ;
        foaf:homepage <https://vocabs.datastations.nl/aatconcepts> ;
        a skos:ConceptScheme .

    ?concept a skos:Concept ;
             skos:inScheme <https://vocabularies.dans.knaw.nl/aatconcepts> ;
             rdfs:label ?label_literal_en ;
             rdfs:label ?label_literal_nl .
            #  dcterms:contributor ?contrib ; 
            #  dcterms:license ?license . 
}

WHERE {


      ?concept a gvp:Concept ;
              skos:inScheme aat: ;
              skosxl:prefLabel ?preflabel .
            # ;
            #  dcterms:contributor ?contrib ; 
            # dcterms:license ?license . 
              
    { ?preflabel  dcterms:language aat:300388277 ;
                  skosxl:literalForm ?label_literal_en. } # lang: @en
                 
    UNION

    { ?preflabel  dcterms:language aat:300387822 ;
                  skosxl:literalForm ?label_literal_en_us . 
      BIND (STRLANG(STR(?label_literal_en_us), 'en') AS  ?label_literal_en)} # lang: @en-US - converts to @en
    
    UNION
    
    { ?preflabel  dcterms:language aat:300388256 ;
                  skosxl:literalForm ?label_literal_nl . } # lang: @nl 

}
ORDER BY ?concept
''' 

construct_results = sparql_query(query=pref_label_query, format='turtle')
print(construct_results)
with open('output_aat_subjects.ttl', 'wb') as att_subjects_f:
    att_subjects_f.write(construct_results)


NameError: name 'sparql_query' is not defined

https://www.w3.org/TR/skos-primer/#secextension  *3.2 Re-using and Extending Concept Schemes* mentions that
> Linking concepts by means of mappings is not the only way to interlink concept schemes. The use of URIs on the Semantic Web allows resources to be shared and reused in a distributed fashion. As a result it is possible for a SKOS concept to participate in several concept schemes at the same time. For example, a SKOS publisher can choose to locally extend an existing concept scheme by declaring any new concepts that may be needed and simply linking to concepts that have already been defined in the existing scheme.

In this case, we are reusing AAT entities with with semantic adaptations, namely
* reusing only the AAT concepts, and excluding structural terms, such as Facets
* making each concept an explicit instance of the `skos:Concept` class, which are only inferred in AAT
* flattening the AAT hierarchy into a controlled vocabulary


Why are we reusing AAT concepts in such way?
* so they can be index by Skosmos

# Publish the extracted terms

In order to publish this extract of AAT, we will need to 
* concept scheme  for the entities (concepts) `a skos:ConceptScheme`

In [4]:

# SIDE NOTE: temporary alphabetical list

# http://vocab.getty.edu/aat/300411913  <temporary alphabetical list: languages and writing systems> 
# includes members which are instances gvp:Concepts which we want to exclude

# QUESTION: shall we try to exclude these concepts from the slim. Don't think so

all_aat_lang_nodes = '''SELECT *
WHERE { 
   ?member gvp:broaderGeneric aat:300389738 . 
   ?member rdfs:label ?label
   } 
''' 

all_aat_lang_nodes_results = sparql_query(query=all_aat_lang_nodes, format='json')
pprint(all_aat_lang_nodes_results)

# aat:300388256	Dutch (language) 
# aat:300388277  English (language) 


{'head': {'vars': ['member', 'label']},
 'results': {'bindings': [{'label': {'type': 'literal',
                                     'value': 'Afro-Asiatic (language family)',
                                     'xml:lang': 'en'},
                           'member': {'type': 'uri',
                                      'value': 'http://vocab.getty.edu/aat/300387783'}},
                          {'label': {'type': 'literal',
                                     'value': 'Afro-Asiatic language',
                                     'xml:lang': 'en'},
                           'member': {'type': 'uri',
                                      'value': 'http://vocab.getty.edu/aat/300387783'}},
                          {'label': {'type': 'literal',
                                     'value': 'Afro-Asiatic languages',
                                     'xml:lang': 'en'},
                           'member': {'type': 'uri',
                                      'value': 'http://vocab.get

# TODOs
* edit - provide content and explain what I am trying to do with slims
* skos metadata
* test output in skosmos